In [30]:
from dotenv import load_dotenv
from typing import Annotated, List, Tuple
from typing_extensions import TypedDict
from langchain.tools import tool, BaseTool
from langchain.schema import Document
from langgraph.graph import StateGraph, START, END, MessagesState
from langgraph.graph.message import add_messages
from langgraph.prebuilt import ToolNode, tools_condition
from langgraph.checkpoint.memory import MemorySaver
from langchain_openai import ChatOpenAI
from langchain_core.prompts import ChatPromptTemplate, SystemMessagePromptTemplate, AIMessagePromptTemplate, HumanMessagePromptTemplate
from langchain.schema import SystemMessage, HumanMessage, AIMessage
from langchain.retrievers.multi_query import MultiQueryRetriever
import gradio as gr

from IPython.display import Image, display
import sys
import os
import uuid


load_dotenv('/Users/nadaa/Documents/code/py_innovations/srf_chatbot_v2/.env')

sys.path.append(os.path.abspath('..'))
%load_ext autoreload
%autoreload 2

import src.utils.qdrant_manager as qm
import prompts.system_prompts as sp





The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [31]:
class ToolManager:
    def __init__(self, collection_name="openai_large_chunks_1500char"):
        self.tools = []
        self.qdrant = qm.QdrantManager(collection_name=collection_name)
        self.vectorstore = self.qdrant.get_vectorstore()
        self.add_vector_search_tool()

    def get_tools(self):
        return self.tools

    def add_vector_search_tool(self):
        @tool
        def vector_search(query: str, k: int = 5) -> list[Document]:
            """Useful for simple queries. This tool will search a vector database for passages from the teachings of Paramhansa Yogananda and other publications from the Self Realization Fellowship (SRF).
            The user has the option to specify the number of passages they want the search to return, otherwise the number of passages will be set to the default value."""
            retriever = self.vectorstore.as_retriever(search_kwargs={"k": k})
            documents = retriever.invoke(query)
            return documents
        
        
        @tool
        def multiple_query_vector_search(query: str, k: int = 5) -> list[Document]:
            """Useful when the user's query is vague, complex, or involves multiple concepts. 
            This tool will write multiple versions of the user's query and search the vector database for relevant passages. 
            Returns a list of relevant passages."""
            
            llm = ChatOpenAI(model="gpt-4o-mini", temperature=0.5)
            retriever_from_llm = MultiQueryRetriever.from_llm(retriever=self.vectorstore.as_retriever(), llm=llm)
            documents = retriever_from_llm.invoke(query)
            return documents
        
        
        self.tools.append(vector_search)
        self.tools.append(multiple_query_vector_search)

In [32]:

class SRFChatbot:
    def __init__(
        self,
        chatbot_instructions: str = sp.system_prompt_templates['Open-Ended Bot'],
        model: str = 'gpt-4o-mini',
        temperature: float = 0,
    ):
        # Initialize the LLM and the system message
        self.llm = ChatOpenAI(model=model, temperature=temperature)
        self.system_message = SystemMessage(content=chatbot_instructions)
        self.tools = ToolManager().get_tools()
        self.llm_with_tools = self.llm.bind_tools(self.tools)

        # Build the graph
        self.graph = self.build_graph()
        # Get the configurable
        self.config = self.get_configurable()
    
    def reset_system_prompt(self, chatbot_instructions_dropdown: str):
        # Get chatbot instructions
        chatbot_instructions = sp.system_prompt_templates[chatbot_instructions_dropdown]
        # Reset the system prompt
        self.system_message = SystemMessage(content=chatbot_instructions)
        # Reset the configurable
        self.config = self.get_configurable()

        return chatbot_instructions

    def get_configurable(self):
        # This thread id is used to keep track of the chatbot's conversation
        self.thread_id = str(uuid.uuid4())
        return {"configurable": {"thread_id": self.thread_id}}
        
    # Add the system message onto the llm
    def chatbot(self, state: MessagesState):
        messages = [self.system_message] + state["messages"]
        return {"messages": [self.llm_with_tools.invoke(messages)]}
    
    def build_graph(self):

        # Add chatbot state
        graph_builder = StateGraph(MessagesState)

        # Add nodes
        tool_node = ToolNode(self.tools)
        graph_builder.add_node("tools", tool_node)
        graph_builder.add_node("chatbot", self.chatbot)

        # Add a conditional edge wherein the chatbot can decide whether or not to go to the tools
        graph_builder.add_conditional_edges(
            "chatbot",
            tools_condition,
        )

        # Add fixed edges
        graph_builder.add_edge(START, "chatbot")
        graph_builder.add_edge("tools", "chatbot")

        # Instantiate the memory saver
        memory = MemorySaver()

        # Compile the graph
        return graph_builder.compile(checkpointer=memory)






In [33]:
chatbot = SRFChatbot()


In [15]:
query = "Tell me more about reducing nervousness to improve sleep"
results = chatbot.graph.invoke({"messages": [HumanMessage(content=query)]}, chatbot.config)

In [16]:
print(results['messages'][-1].content)

To reduce nervousness and improve sleep, it is essential to recognize that much of our nervousness stems from our own reactions and emotional states. Paramhansa Yogananda emphasizes that restlessness and emotional excitement can overload the nervous system, leading to fatigue and anxiety. Engaging in deep meditation can help calm the nerves, as it allows the body to rest and rejuvenate. Additionally, dietary choices play a significant role; consuming calming foods such as whole grains, fruits, and avoiding stimulants like caffeine and alcohol can support a healthier nervous system. Practicing silence and reducing exposure to noise can also alleviate nervousness, creating a more peaceful environment conducive to sleep.

**Quotes:**
1. "You always blame other things for making you nervous, but never accuse yourself. Yet it is you who make yourself nervous; ninety-nine percent is your own fault." - *Journey to Self-Realization, Probing the Core of Nervousness*
2. "When you stop overloadin

In [17]:

chatbot.graph.get_state(chatbot.config)[0]['messages']

[HumanMessage(content='Tell me more about reducing nervousness to improve sleep', additional_kwargs={}, response_metadata={}, id='c1d3f9ba-0e06-4a6a-b38c-3dcd3be78bbf'),
 AIMessage(content='', additional_kwargs={'tool_calls': [{'id': 'call_fjyQpF0pjUQZ8gobl2SAozXV', 'function': {'arguments': '{"query":"reducing nervousness improve sleep"}', 'name': 'vector_search'}, 'type': 'function'}], 'refusal': None}, response_metadata={'token_usage': {'completion_tokens': 19, 'prompt_tokens': 433, 'total_tokens': 452, 'completion_tokens_details': {'reasoning_tokens': 0}}, 'model_name': 'gpt-4o-mini-2024-07-18', 'system_fingerprint': 'fp_1bb46167f9', 'finish_reason': 'tool_calls', 'logprobs': None}, id='run-4a39fe1a-6413-4ba3-8aa3-290dc31a27bb-0', tool_calls=[{'name': 'vector_search', 'args': {'query': 'reducing nervousness improve sleep'}, 'id': 'call_fjyQpF0pjUQZ8gobl2SAozXV', 'type': 'tool_call'}], usage_metadata={'input_tokens': 433, 'output_tokens': 19, 'total_tokens': 452}),
 ToolMessage(cont

In [35]:

def respond(query, history):

    formatted_query = [HumanMessage(content=query)]
    # Invoke the graph with properly formatted input
    result = chatbot.graph.invoke({"messages": formatted_query}, chatbot.config)
    
    # Extract the assistant's response
    response = result["messages"][-1].content

    history.append((query, response))

    
    return history

chatbot = SRFChatbot()

# Gradio interface with responsive layout
with gr.Blocks(css="""
    @media (max-width: 600px) {
        .gr-row { flex-direction: column !important; }
        .gr-column { width: 100% !important; }
    }
""") as demo:
    gr.Markdown("# SRF Chatbot")
    
    with gr.Row(elem_classes="gr-row"):
        with gr.Column(scale=4, elem_classes="gr-column"):
            chatbot_output = gr.Chatbot()
            user_input = gr.Textbox(placeholder="Type your question here...")
            submit_button = gr.Button("Submit")
        
        with gr.Column(scale=1, elem_classes="gr-column"):
            system_prompt_dropdown = gr.Dropdown(
                choices=list(sp.system_prompt_templates.keys()),
                label="Select Chatbot Instructions",
                value=list(sp.system_prompt_templates.keys())[0]
            )
            system_prompt_display = gr.Textbox(
                value=sp.system_prompt_templates[list(sp.system_prompt_templates.keys())[0]],
                label="Current Chatbot Instructions",
                lines=5,
                interactive=False
            )
    
    # Update system prompt display when a new prompt is selected
    system_prompt_dropdown.change(
        fn=chatbot.reset_system_prompt,
        inputs=[system_prompt_dropdown],
        outputs=[system_prompt_display]
    )
    
    # Submit button logic to handle chatbot conversation
    submit_button.click(
        fn=respond,
        inputs=[user_input, chatbot_output],
        outputs=[chatbot_output]
    )


demo.launch()


Running on local URL:  http://127.0.0.1:7875

To create a public link, set `share=True` in `launch()`.


In [43]:
import gradio as gr

# Define the respond function
def respond(query, history):
    formatted_query = [HumanMessage(content=query)]
    # Invoke the graph with properly formatted input
    result = chatbot.graph.invoke({"messages": formatted_query}, chatbot.config)
    
    # Extract the assistant's response
    response = result["messages"][-1].content

    history.append((query, response))

    return history, ""

# Initialize chatbot
chatbot = SRFChatbot()

# Gradio interface with black and grey color scheme
with gr.Blocks(css="""
    .gradio-container {
        background-color: #F0F0F0; 
        font-family: 'Arial', sans-serif;
    }
    h1, h2, p {
        color: black;
    }
    h1 {
        font-size: 32px;
        text-align: left;
    }
    h2 {
        font-size: 24px;
    }
    p {
        font-size: 18px;
        margin-bottom: 15px;
    }
    .gr-button {
        background-color: #333333; 
        color: white;
        font-size: 18px;
        padding: 10px;
    }
    .gr-textbox textarea {
        font-size: 18px;
        color: black;
    }
    .gr-dropdown {
        font-size: 18px;
        color: black;
    }
    .source-box {
        background-color: #D0D0D0; 
        padding: 10px; 
        border-radius: 8px; 
        margin-top: 20px;
        color: black;
    }
    @media (max-width: 600px) {
        .gr-row { flex-direction: column !important; }
        .gr-column { width: 100% !important; }
    }
""") as demo:
    
    # Title
    gr.Markdown("# SRF Chatbot")
    
    with gr.Row(elem_classes="gr-row"):
        with gr.Column(scale=4, elem_classes="gr-column"):
            # Chatbot interface
            chatbot_output = gr.Chatbot()
            user_input = gr.Textbox(placeholder="Type your question here...", label="Your Question")
            submit_button = gr.Button("Submit")
        
        with gr.Column(scale=1, elem_classes="gr-column"):
            # Dropdown to select system prompts
            system_prompt_dropdown = gr.Dropdown(
                choices=list(sp.system_prompt_templates.keys()),
                label="Select Chatbot Instructions",
                value=list(sp.system_prompt_templates.keys())[0],
                elem_classes="gr-dropdown"
            )
            # Display the selected system prompt
            system_prompt_display = gr.Textbox(
                value=sp.system_prompt_templates[list(sp.system_prompt_templates.keys())[0]],
                label="Current Chatbot Instructions",
                lines=5,
                interactive=False
            )
            
            # Sources box
            gr.Markdown("""
            <div class="source-box">
                <strong>Available sources:</strong>
                <ul>
                    <li>Journey to Self-Realization</li>
                    <li>The Second Coming of Christ</li>
                    <li>Autobiography of a Yogi</li>
                </ul>
            </div>
            """)
    
    # Update system prompt display when a new prompt is selected
    system_prompt_dropdown.change(
        fn=chatbot.reset_system_prompt,
        inputs=[system_prompt_dropdown],
        outputs=[system_prompt_display]
    )
    
    # Submit button logic to handle chatbot conversation
    submit_button.click(
        fn=respond,
        inputs=[user_input, chatbot_output],
        outputs=[chatbot_output, user_input]
    )

# Launch the interface
demo.launch()


Running on local URL:  http://127.0.0.1:7883

To create a public link, set `share=True` in `launch()`.


In [44]:
import gradio as gr
import src.srf_bot as sb
import prompts.system_prompts as sp
from langchain_core.messages import HumanMessage    

# Define the respond function
def respond(query, history):
    formatted_query = [HumanMessage(content=query)]
    # Invoke the graph with properly formatted input
    result = chatbot.graph.invoke({"messages": formatted_query}, chatbot.config)
    
    # Extract the assistant's response
    response = result["messages"][-1].content

    history.append((query, response))

    return history, ""

# Initialize chatbot
chatbot = sb.SRFChatbot()

# Gradio interface with black and grey color scheme
with gr.Blocks(css="""
    .gradio-container {
        background-color: #F0F0F0; 
        font-family: 'Arial', sans-serif;
    }
    h1, h2, p {
        color: black;
    }
    h1 {
        font-size: 32px;
        text-align: left;
    }
    h2 {
        font-size: 24px;
    }
    p {
        font-size: 18px;
        margin-bottom: 15px;
    }
    .gr-button {
        background-color: #333333; 
        color: white;
        font-size: 18px;
        padding: 10px;
    }
    .gr-textbox textarea {
        font-size: 18px;
        color: black;
    }
    .gr-dropdown {
        font-size: 18px;
        color: black;
    }
    .source-box {
        background-color: white; 
        padding: 10px; 
        border-radius: 8px; 
        margin-top: 20px;
        color: black;
        border: 1px solid #D0D0D0;
    }
    @media (max-width: 600px) {
        .gr-row { flex-direction: column !important; }
        .gr-column { width: 100% !important; }
    }
""") as demo:
    
    # Title
    gr.Markdown("# SRF Chatbot")
    
    with gr.Row(elem_classes="gr-row"):
        with gr.Column(scale=4, elem_classes="gr-column"):
            # Chatbot interface
            chatbot_output = gr.Chatbot(height=600)  # Increased height for longer chat interface
            user_input = gr.Textbox(placeholder="Type your question here...", label="Your Question")
            submit_button = gr.Button("Submit")
        
        with gr.Column(scale=1, elem_classes="gr-column"):
            # Dropdown to select system prompts
            system_prompt_dropdown = gr.Dropdown(
                choices=list(sp.system_prompt_templates.keys()),
                label="Select Chatbot Instructions",
                value=list(sp.system_prompt_templates.keys())[0],
                elem_classes="gr-dropdown"
            )
            # Display the selected system prompt
            system_prompt_display = gr.Textbox(
                value=sp.system_prompt_templates[list(sp.system_prompt_templates.keys())[0]],
                label="Current Chatbot Instructions",
                lines=5,
                interactive=False
            )
            
            # Sources box (Now white, matching the other boxes)
            gr.Markdown("""
            <div class="source-box">
                <strong>Available sources:</strong>
                <ul>
                    <li>Journey to Self-Realization</li>
                    <li>The Second Coming of Christ</li>
                    <li>Autobiography of a Yogi</li>
                </ul>
            </div>
            """)
    
    # Update system prompt display when a new prompt is selected
    system_prompt_dropdown.change(
        fn=chatbot.reset_system_prompt,
        inputs=[system_prompt_dropdown],
        outputs=[system_prompt_display]
    )
    
    # Submit button logic to handle chatbot conversation
    submit_button.click(
        fn=respond,
        inputs=[user_input, chatbot_output],
        outputs=[chatbot_output, user_input]
    )

# Launch the interface
demo.launch()


Running on local URL:  http://127.0.0.1:7885

To create a public link, set `share=True` in `launch()`.
